# MODFLOW 6: Accessing Simulation Settings, Models, and Packages

This tutorial shows how to view, access, and change the underlying package
variables for MODFLOW 6 objects in FloPy.  Interaction with a FloPy
MODFLOW 6 model is different from other models, such as MODFLOW-2005,
MT3D, and SEAWAT, for example.

The MODFLOW 6 simulation structure is arranged in the following
generalized way:

>       SIMULATION --> PACKAGE --> Data
>
>       SIMULATION --> MODEL --> PACKAGE (--> PACKAGE) --> Data

This tutorial focuses on accessing simulation-wide FloPy settings and
how to create and access models and packages.  Tutorial 3, 4, and 5 offer a
more in depth look at observation, time series, and time array series
packages, and tutorial 6, 7, 8, and 9 offer a more in depth look at the data.

## Create Simple Demonstration Model

This tutorial uses a simple demonstration simulation with one GWF Model.
The model has 3 layers, 4 rows, and 5 columns.  The model is set up to
use multiple model layers in order to demonstrate some of the layered
functionality in FloPy.

In [1]:
# package import
from tempfile import TemporaryDirectory

In [2]:
import flopy

In [3]:
temp_dir = TemporaryDirectory()
workspace = temp_dir.name
name = "tutorial01_mf6_data"

In [4]:
# set up simulation and basic packages
sim = flopy.mf6.MFSimulation(sim_name=name, sim_ws=workspace)
flopy.mf6.ModflowTdis(
    sim, nper=10, perioddata=[[365.0, 1, 1.0] for _ in range(10)]
)
flopy.mf6.ModflowIms(sim)
gwf = flopy.mf6.ModflowGwf(sim, modelname=name, save_flows=True)
flopy.mf6.ModflowGwfdis(gwf, nlay=3, nrow=4, ncol=5)
flopy.mf6.ModflowGwfic(gwf)
flopy.mf6.ModflowGwfnpf(gwf, save_specific_discharge=True)
flopy.mf6.ModflowGwfchd(
    gwf, stress_period_data=[[(0, 0, 0), 1.0], [(2, 3, 4), 0.0]]
)
budget_file = f"{name}.bud"
head_file = f"{name}.hds"
flopy.mf6.ModflowGwfoc(
    gwf,
    budget_filerecord=budget_file,
    head_filerecord=head_file,
    saverecord=[("HEAD", "ALL"), ("BUDGET", "ALL")],
)
print("Done creating simulation.")

Done creating simulation.


## Accessing Simulation-Level Settings

FloPy has a number of settings that can be set for the entire simulation.
These include how much information FloPy writes to the console, how to
format the MODFLOW package files, and whether to verify MODFLOW data.

The verbosity level, which determines how much FloPy writes to command line
output.  The options are 1 for quiet, 2 for normal, and 3 for verbose.
Below we set the verbosity level to verbose.

In [5]:
sim.simulation_data.verbosity_level = 3

We can also set the number of spaces to indent data when writing package
files by setting the indent string.

In [6]:
sim.simulation_data.indent_string = "    "

Next we set the precision and number of characters written for floating
point variables.

In [7]:
sim.float_precision = 8
sim.float_characters = 15

Lastly, we disable verify_data and auto_set_sizes for faster performance.
With these options disabled FloPy will not do any checking or autocorrecting
of your data.

In [8]:
sim.verify_data = False
sim.auto_set_sizes = False

## Accessing Models and Packages

At this point a simulation is available in memory.  In this particular case
the simulation was created directly using Python code; however, the
simulation might also have been loaded from existing model files using
the `FloPy.mf6.MFSimulation.load()` function.

Once a MODFLOW 6 simulation is available in memory, the contents of the
simulation object can be listed using a simple print command.

In [9]:
print(sim)

sim_name = tutorial01_mf6_data
sim_path = /tmp/tmpk1k8g5og
exe_name = mf6

###################
Package mfsim.nam
###################

package_name = mfsim.nam
filename = mfsim.nam
package_type = nam
model_or_simulation_package = simulation
simulation_name = tutorial01_mf6_data


###################
Package tutorial01_mf6_data.tdis
###################

package_name = tutorial01_mf6_data.tdis
filename = tutorial01_mf6_data.tdis
package_type = tdis
model_or_simulation_package = simulation
simulation_name = tutorial01_mf6_data


###################
Package ims_-1
###################

package_name = ims_-1
filename = tutorial01_mf6_data.ims
package_type = ims
model_or_simulation_package = simulation
simulation_name = tutorial01_mf6_data


@@@@@@@@@@@@@@@@@@@@
Model tutorial01_mf6_data
@@@@@@@@@@@@@@@@@@@@

name = tutorial01_mf6_data
model_type = gwf6
version = mf6
model_relative_path = .

###################
Package dis
###################

package_name = dis
filename = tutorial01_mf6_data.

Simulation-level packages, models, and model packages can be shown by
printing the simulation object.  In this case, you should see the
all of the contents of simulation and some information about each FloPy
object that is part of simulation.

To get the `TDIS` package and print the contents, we can do the following

In [10]:
tdis = sim.tdis
print(tdis)

package_name = tutorial01_mf6_data.tdis
filename = tutorial01_mf6_data.tdis
package_type = tdis
model_or_simulation_package = simulation
simulation_name = tutorial01_mf6_data

Block dimensions
--------------------
nper
{internal}
(10)


Block perioddata
--------------------
perioddata
{internal}
([(365., 1, 1.) (365., 1, 1.) (365., 1, 1.) (365., 1, 1.) (365., 1, 1.)
 (365., 1, 1.) (365., 1, 1.) (365., 1, 1.) (365., 1, 1.) (365., 1, 1.)])





To get the Iterative Model Solution (`IMS`) object, we use the following
syntax

In [11]:
ims = sim.get_package("ims_-1")
print(ims)

package_name = ims_-1
filename = tutorial01_mf6_data.ims
package_type = ims
model_or_simulation_package = simulation
simulation_name = tutorial01_mf6_data




Or because there is only one `IMS` object for this simulation, we can
access it as

In [12]:
ims = sim.get_package("ims")
print(ims)

package_name = ims_-1
filename = tutorial01_mf6_data.ims
package_type = ims
model_or_simulation_package = simulation
simulation_name = tutorial01_mf6_data




When printing the sim object, there is also a simulation package called
nam.  This package contains the information that is written to the
`mfsim.nam` file, which is the primary file that MODFLOW 6 reads when it
first starts.  The nam package is automatically updated for you by FloPy and
does not require modification.

In [13]:
nam = sim.get_package("nam")
print(nam)

package_name = mfsim.nam
filename = mfsim.nam
package_type = nam
model_or_simulation_package = simulation
simulation_name = tutorial01_mf6_data

Block timing
--------------------
tdis6
{internal}
(tutorial01_mf6_data.tdis)


Block models
--------------------
models
{internal}
([('gwf6', 'tutorial01_mf6_data.nam', 'tutorial01_mf6_data')])


Block solutiongroup
--------------------
solutiongroup
{internal}
([('ims6', 'tutorial01_mf6_data.ims', 'tutorial01_mf6_data')])





To see the models that are contained within the simulation, we can get a
list of their names as follows

In [14]:
print(sim.model_names)

['tutorial01_mf6_data']


`sim.model_names` returns the keys of an ordered dictionary, which isn't very
useful to us, but we can convert that to a list and then go through that
list and print information about each model in the simulation.  In this
case there is only one model, but had there been more models, we would
see them listed here

In [15]:
model_names = list(sim.model_names)
for mname in model_names:
    print(mname)

tutorial01_mf6_data


If we want to get a model from a simulation, then we use the `get_model()`
method of the sim object.  Here we go through all the models in the
simulation and print the model name and the model type.

In [16]:
model_names = list(sim.model_names)
for mname in model_names:
    m = sim.get_model(mname)
    print(m.name, m.model_type)

tutorial01_mf6_data gwf6


For this simple case here with only one `GWF` model, we can very easily get
the FloPy representation of the `GWF` model as

In [17]:
gwf = sim.get_model(name)

Now that we have the `GWF` object, we can print it, and see what's it
contains.

In [18]:
print(gwf)

name = tutorial01_mf6_data
model_type = gwf6
version = mf6
model_relative_path = .

###################
Package dis
###################

package_name = dis
filename = tutorial01_mf6_data.dis
package_type = dis
model_or_simulation_package = model
model_name = tutorial01_mf6_data


###################
Package ic
###################

package_name = ic
filename = tutorial01_mf6_data.ic
package_type = ic
model_or_simulation_package = model
model_name = tutorial01_mf6_data


###################
Package npf
###################

package_name = npf
filename = tutorial01_mf6_data.npf
package_type = npf
model_or_simulation_package = model
model_name = tutorial01_mf6_data


###################
Package chd_0
###################

package_name = chd_0
filename = tutorial01_mf6_data.chd
package_type = chd
model_or_simulation_package = model
model_name = tutorial01_mf6_data


###################
Package oc
###################

package_name = oc
filename = tutorial01_mf6_data.oc
package_type = oc
model_

What we see here is the information that we saw when we printed the sim
object.

One of the most common operations on a model is to see what packages are in
it and then get packages of interest.  A list of packages in a model can
obtained as

In [19]:
package_list = gwf.get_package_list()
print(package_list)

['DIS', 'IC', 'NPF', 'CHD_0', 'OC']


As you might expect we can access each package in this list with
gwf.get_package().  Thus, the following syntax can be used to obtain and
print the contents of the `DIS` Package

In [20]:
dis = gwf.get_package("dis")
print(dis)

package_name = dis
filename = tutorial01_mf6_data.dis
package_type = dis
model_or_simulation_package = model
model_name = tutorial01_mf6_data

Block dimensions
--------------------
nlay
{internal}
(3)

nrow
{internal}
(4)

ncol
{internal}
(5)


Block griddata
--------------------
delr
{constant 1.0}

delc
{constant 1.0}

top
{constant 1.0}

botm
{constant 0.0}





The Python type for this dis package is simply

In [21]:
print(type(dis))

<class 'flopy.mf6.modflow.mfgwfdis.ModflowGwfdis'>


In [22]:
try:
    temp_dir.cleanup()
except PermissionError:
    # can occur on windows: https://docs.python.org/3/library/tempfile.html#tempfile.TemporaryDirectory
    pass